# Exercise 1: Parsing programming languages

In this exercise, you will be writting a parser for the KL language which has the following syntax:

We will use the [lark](https://lark-parser.readthedocs.io/en/latest/) library.

Requirements
--------------------

In [ ]:
from lark import Lark

## Parser for function call

We are going to start with a only supporting function calls

```
Statements: (Expr (';' | '\n') )* Expr?
Expr: Identifier | FunctionCall | Number
FunctionCall: Identifier '(' Arguments? ')'
Arguments: Expr ( ',' Expr )*
Identifier: ([a-z]|[A-Z])+
Number: [0-9]+('.'[0-9]+)?('e'-?[0-9]+)?
```

The following statement create the parser, you should modify it to implement the full grammar.
The lark parser use a syntax similar to BNF, with a few noteworthy points:

- non-terminals should be lower-case, and terminals should be upper case or in ""
- when defining a non-terminal, you start on a new line with '?', for instance '?expr' and then refer to it without the '?', for instance 'expr'
- '|' indicates an alternative '?' indicates optional '+' indicates one or more '*' indicates 0 or more
- A number of token are predefined in lark and are imported in our grammar with `%import` keyword, in the statement below, you don't need to change any of the import, they are correct
- '-> name' (ie -> identifier) ensure that Lark creates a Tree object for the line, while not strictly necesserary for this exercise, it will be needed for the labs. Also we don't need to use one for expression or statements.

In [ ]:
fc_parser = Lark("""?start: statements
    ?statements: ((expr (";" | NEWLINE) | NEWLINE ) )* expr?
    ?expr: identifier | number

    ?identifier: NAME -> identifier
    ?number: NUMBER -> number

    %import common.NEWLINE
    %import common.CNAME -> NAME
    %import common.NUMBER
    %import common.WS_INLINE
    %ignore WS_INLINE
    COMMENT: "/*" /(.|\n)+/x "*/" | "//" /.+/
    %ignore COMMENT
""")

### Tests

In [ ]:
fc_parser.parse("add(1,2)")

In [ ]:
fc_parser.parse("add(pi, mul(2.12, div(3.1e2,41e-3)))")

In [ ]:
fc_parser.parse("""// This is a comment
add(1,2) /* this is an other comment */

add(pi, mul(2.12, div(3.1e2,41e-3)))""")

In [ ]:
tree = fc_parser.parse("add(1,2); mul(2,3)")
assert(tree.data == "statements")

In [ ]:
tree = fc_parser.parse("a(1,1)")
assert(tree.data == "functioncall")
assert(tree.children[1].data == "arguments")

In [ ]:
tree = fc_parser.parse("1")
assert(tree.data == "number")

## Handle assignments

We are extending our grammar to handle assignments:

```
Statements: (Expr (';' | '\n') )* Expr?
Expr:Identifier | FunctionCall | Number | Define | Assignment
FunctionCall: Identifier '(' Arguments? ')'
Arguments: Expr ( ',' Expr )*
Define: 'define' Identifier ( '=' Expr )?
Assignment: Identifier '=' Expr
Identifier: ([a-z]|[A-Z])+
Number: [0-9]+('.'[0-9]+)?('e'-?[0-9]+)?
```

Extend the previous parser to handle assignments:

In [ ]:
fca_parser = Lark("""
""")

### Tests

In [ ]:
fca_parser.parse("define a = add(pi, mul(2.12, div(3.1e2,41e-3)))")

In [ ]:
fca_parser.parse("define b; b = 10")

In [ ]:
fca_parser.parse("""define a = add(pi, mul(2.12, div(3.1e2,41e-3)))
add(1,a)""")

In [ ]:
tree = fca_parser.parse("add(1,2); mul(2,3)")
assert(tree.data == "statements")

In [ ]:
tree = fca_parser.parse("a(1,1)")
assert(tree.data == "functioncall")
assert(tree.children[1].data == "arguments")

In [ ]:
tree = fca_parser.parse("1")
assert(tree.data == "number")

In [ ]:
tree = fca_parser.parse("define a = 1")
assert(tree.data == "define")

In [ ]:
tree = fca_parser.parse("a = 1")
assert(tree.data == "assignment")

## KL Parser

Expand your grammar so that it can handle the full KL syntax, for the functional paradigm:

```
Statements: (Expr (';' | '\n') )* Expr?
Expr:Identifier | FunctionCall | Number | Define | Assignment | Function
FunctionCall: Identifier '(' Arguments? ')'
Arguments: Expr ( ',' Expr )*
Define: 'define' Identifier ( '=' Expr )?
Assignment: Identifier '=' Expr
Function: 'function' '(' Parameters? ')' '->' Identifier Block
Block: '{' Statements '}'
Parameters: Identifier ( ',' Identifier )*
Identifier: ([a-z]|[A-Z])+
Number: [0-9]+('.'[0-9]+)?('e'-?[0-9]+)?
```


In [ ]:
kl_parser = Lark("""
""")

### Tests

In [ ]:
kl_parser.parse("define f = function(a,b) -> c { c = add(pi, mul(a, div(b,41e-3))) }")

In [ ]:
kl_parser.parse("define f = function(a,b) -> c { define d = add(10, a) ; c = add(pi, mul(d, div(d, b))) }")

In [ ]:
kl_parser.parse("""// test
define f1 = function(a,b) -> c { c = add(pi, mul(a, div(b,41e-3))) } /* test comment */
define f2 = function(a,b) -> c { define d = f1(10, a) ; c = add(pi, mul(d, div(d, b))) }
f2(3,4); // hallo""")

If one of the test bellow fails, you may need to add a "-> name" in your lark definition. For instance:

```bnf
 ?identifier: NAME
```

to

```bnf
 ?identifier: NAME -> identifier
```

This is needed for the kl interpreter in Lab 1,2,3.

In [ ]:
tree = kl_parser.parse("define b = 2;")
assert(tree.data == "define")

In [ ]:
tree = kl_parser.parse("a")
assert(tree.data == "identifier")

In [ ]:
tree = kl_parser.parse("a(1,1)")
assert(tree.data == "functioncall")
assert(tree.children[1].data == "arguments")

In [ ]:
tree = kl_parser.parse("a(1)")
assert(tree.data == "functioncall")
assert(tree.children[1].data == "arguments")

In [ ]:
tree = kl_parser.parse("1")
assert(tree.data == "number")

In [ ]:
tree = kl_parser.parse("define a = 1")
assert(tree.data == "define")

In [ ]:
tree = kl_parser.parse("define a")
assert(tree.data == "define")

In [ ]:
tree = kl_parser.parse("a = 1")
assert(tree.data == "assignment")

In [ ]:
tree = kl_parser.parse("function(a,b) -> c { c = add(pi, mul(a, div(b,41e-3))) }")
assert(tree.data == "function")

In [ ]:
tree = kl_parser.parse("function() -> c { c = 2 }")
assert(tree.data == "function")

In [ ]:
tree = kl_parser.parse("a = 1; b = 2")
assert(tree.data == "statements")

## KL Simple expression interpreter

In this exercise we will implement a calc function for evaluating simple expression. The main goal is for you to get an understanding of the lark API for trees.

We will implement a recursive 'calc' function that can computed basic expressions such as ```add(3, mul(2, div(4,2)))```. If you look bellow you can see the introspection result of parsing a KL expressions with lark.

In [ ]:
tree = kl_parser.parse("add(3, mul(2, div(4,2)))")
print("data:", tree.data)
print("children: ")
for c in tree.children:
    print(" -", c)
print("pretty:")
print(tree.pretty('        '))

As we can see, there are basically two types of elements in a tree, ```Tree``` and ```Token```. Tokens are terminals, they have the following fields:

- data: which identifies which rules triggered the token, this can generaly be ignored.
- value: which contains the actual value of the token, as a string.

Trees are non-terminals, they have the following fields:

- data: which identifies the rules that triggered the creation of the tree, for the calc function, this can be ```number```, ```identifier```, ```functioncall``` or ```arguments```.
- children: a collection of ```Tree``` or ```Token```


### Calc

Implement a simple recursive ```calc``` function, to illustrate we have already implemented ```number``` for you, you will need to implement support for ```identifier``` and ```functioncall```. To evaluate the arguments of ```functioncall```, you should call ```calc``` recursively.

In [ ]:
def calc(tree):
    if tree.data == "number":
        return float(tree.children[0].value)
    else:
        print("data:", tree.data)
        print("children: ")
        for c in tree.children:
            print(" -", c)
        print("pretty:")
        print(tree.pretty('        '))
        raise Exception("Error")


### Test

In [ ]:
assert(calc(kl_parser.parse("2")) == 2)

In [ ]:
assert(calc(kl_parser.parse("pi")) == 3.14)

In [ ]:
assert(calc(kl_parser.parse("sub(3, 1)")) == 2)

In [ ]:
assert(calc(kl_parser.parse("add(3, mul(2, div(4,2)))")) == 7)